## Playing with Fishing Gym

In [47]:
import gym_fishing
import gym
import math
import random
from math import floor
import bokeh.plotting
import numpy as np
import bokeh.io
from itertools import count
import bokeh.plotting
from bokeh.models import Span

bokeh.io.output_notebook()

Loading BokehJS ...

I write a function to find the first point where the trajectory crosses the threshold. I used 100 in the plots shown below.

In [48]:
def find_collapse_point(trajectory, thresh):
    indices = np.where(trajectory < thresh)[0]
    try:
        return np.min(indices)
    except:
        return None

Now I make plots of 100 trajectories. Here I choose a random harvest quota at each season. The red line shows the average time to collapse.

In [49]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
rewards = []

for sample in range(n_samples):
    env.random_reset()
    sample_traj = [env.fish_population]
    for season in range(100):
        if env.fish_population:
            env.step(random.randrange(env.fish_population) / 1e4)
        else:
            break
        sample_traj.append(env.fish_population)
    rewards.append(env.reward)
    sample_traj = np.array(sample_traj)
    collapse_point = find_collapse_point(sample_traj, 100)
    if collapse_point:
        collapse_points.append(collapse_point)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)

vline = Span(location=np.mean(collapse_points), dimension='height', line_color='red', line_width=1)
plot.renderers.extend([vline])
bokeh.io.show(plot)
env.close()

In [50]:
np.mean(rewards)

0.5562261

Complete wipe out, aka harvesting $K$ at $t=0$

In [51]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
rewards = []
# 
for sample in range(n_samples):
    env.random_reset()
    sample_traj = [env.fish_population]
    for season in range(100):
        if env.fish_population:
            if env.fish_population > 5.5e4:
                env.step(max(0, floor(env.fish_population - env.K/2 + env.r*env.fish_population \
                                * (1 - env.fish_population / env.K) ) / 1e4))
            if env.fish_population < 4.5e4:
                env.step(0)
            else:
                env.step(max(0, floor(env.r*env.fish_population \
                                * (1 - env.fish_population / env.K) ) / 1e4))
        else:
            break
        sample_traj.append(env.fish_population)
    rewards.append(env.reward)
    sample_traj = np.array(sample_traj)
    collapse_point = find_collapse_point(sample_traj, 100)
    if collapse_point:
        collapse_points.append(collapse_point)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)


bokeh.io.show(plot)
env.close()

In [52]:
np.mean(rewards)

2.4565151

Here I choose $ \frac{r x}{2}$ quota at each season. The red line shows the average time to collapse.

In [53]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
rewards = []
for sample in range(n_samples):
    env.reset()
    sample_traj = [env.fish_population]
    for season in range(100):
        env.step(floor(env.r * env.fish_population / 2) / 1e4 )
        sample_traj.append(env.fish_population)
    rewards.append(env.reward)
    sample_traj = np.array(sample_traj)
    collapse_point = find_collapse_point(sample_traj, 100)
    if collapse_point:
        collapse_points.append(collapse_point)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)

    
#vline = Span(location=np.mean(collapse_points), dimension='height', line_color='red', line_width=1)
#plot.renderers.extend([vline])
bokeh.io.show(plot)
env.close()

In [54]:
np.mean(rewards)

2.8682998

No harvesting, the orange line shows the analytic solution for how the population should behave.

In [55]:
def logistic_growth_analytic(t, N_init):
    return env.K / (1 + (env.K - N_init) / N_init * np.exp(- env.r * t))

In [56]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
rewards = []
RESET_N = 2e5
for sample in range(n_samples):
    env.reset(RESET_N)
    sample_traj = [env.fish_population]
    for season in range(100):
        env.step(0)
        sample_traj.append(env.fish_population)
    rewards.append(env.reward)
    sample_traj = np.array(sample_traj)
    collapse_point = find_collapse_point(sample_traj, 100)
    if collapse_point:
        collapse_points.append(collapse_point)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)

t = np.linspace(0,100,101)
plot.line(t, logistic_growth_analytic(t, RESET_N), color='orange', line_width=5)
bokeh.io.show(plot)
env.close()

In [57]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
rewards = []
RESET_N = 2e3
for sample in range(n_samples):
    env.reset(RESET_N)
    sample_traj = [env.fish_population]
    for season in range(100):
        env.step(0)
        sample_traj.append(env.fish_population)
    rewards.append(env.reward)
    sample_traj = np.array(sample_traj)
    collapse_point = find_collapse_point(sample_traj, 100)
    if collapse_point:
        collapse_points.append(collapse_point)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)

t = np.linspace(0,100,101)
plot.line(t, logistic_growth_analytic(t, RESET_N), color='orange', line_width=5)
bokeh.io.show(plot)
env.close()

Now attempting to implement deep Q-learning to choose the fishing quota at each season. Heavily borrowing from the Q-learning tutorial from pytorch (https://pytorch.org/tutorials/intermediate/reinforcement_q_learning.html).

In [27]:
import gym
import math
import random
import numpy as np
from collections import namedtuple
from itertools import count
from copy import deepcopy
import torch
import torch.nn as nn
from torch.nn.utils.clip_grad import clip_grad_norm_
import torch.optim as optim
import torch.nn.functional as F
import torchvision.transforms as T

env = gym.make('fishing-v0')

# if gpu is to be used
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Setting up a named tuple and ReplayMemory class to access past transitions.

In [28]:
Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward'))


class ReplayMemory(object):

    def __init__(self, capacity):
        self.capacity = capacity
        self.memory = []
        self.position = 0

    def push(self, *args):
        """Saves a transition."""
        if len(self.memory) < self.capacity:
            self.memory.append(None)
        self.memory[self.position] = Transition(*args)
        self.position = (self.position + 1) % self.capacity

    def sample(self, batch_size):
        return random.sample(self.memory, batch_size)

    def __len__(self):
        return len(self.memory)

Building neural network with 1 hidden layer

In [67]:
class DQN(nn.Module):
    def __init__(self, input_size, hidden_size, num_quotas):
        super(DQN, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, num_quotas)
        #self.fc3 = nn.Linear(hidden_size, num_quotas)
    def forward(self, x):
        out = self.fc1(x)
        out = F.leaky_relu(out)
        out = self.fc2(out)
        #out = F.leaky_relu(out)
        #out = self.fc3(out)
        
        return out

Now onto training,

In [65]:
BATCH_SIZE = 100
GAMMA = 1
EPS_START = 0.99999
EPS_END = 0.01
EPS_DECAY = 1e9
TARGET_UPDATE = 1e2
LAYER_WIDTH = 1000
N_ACTIONS = len(env.action_space)

policy_net = DQN(1, LAYER_WIDTH, N_ACTIONS).to(device).requires_grad_(requires_grad=True)
target_net = DQN(1, LAYER_WIDTH, N_ACTIONS).to(device).requires_grad_(requires_grad=False)
target_net.load_state_dict(policy_net.state_dict())
target_net.eval()

optimizer = optim.SGD(policy_net.parameters(), lr=0.00001)
memory = ReplayMemory(50)

steps_done = 0

def select_action(state):
    global steps_done
    sample = random.random()
    eps_threshold = EPS_END + (EPS_START - EPS_END) * \
        math.exp(-1. * steps_done / EPS_DECAY)
    steps_done += 1
    if sample > eps_threshold:
        with torch.no_grad():
            # So here I find the index of the max Q(S,A)
            # I map the indices of my output to the indices of 
            # action space, so I use this index to access the 
            # corresponding action
            max_index = policy_net(state).max(0)[1]

            return torch.tensor([[env.action_space[max_index]]], device=device, dtype=torch.float)
    # Returning a random action
    else:
        return torch.tensor([[env.action_space[random.randrange(N_ACTIONS)]]], device=device, dtype=torch.float)

In [19]:
x = deepcopy(list(policy_net.parameters()))
x

[Parameter containing:
 tensor([[-6.6272e-01],
         [-9.3421e-01],
         [ 2.4382e-01],
         [-2.1888e-02],
         [-7.9709e-01],
         [-3.0864e-01],
         [ 8.6694e-01],
         [-5.7117e-01],
         [-8.0927e-01],
         [ 7.1997e-01],
         [ 1.5304e-01],
         [ 1.9370e-01],
         [-9.9687e-01],
         [-8.0744e-01],
         [ 8.8017e-01],
         [-6.1021e-01],
         [-2.2539e-01],
         [ 4.6383e-01],
         [ 9.5623e-01],
         [-2.2384e-01],
         [ 3.6994e-01],
         [-1.5507e-01],
         [-5.5755e-01],
         [ 2.5781e-01],
         [-6.5790e-01],
         [ 6.1994e-01],
         [-4.5723e-01],
         [-3.4496e-01],
         [-8.2718e-01],
         [ 8.5781e-01],
         [ 5.5674e-01],
         [-8.8604e-01],
         [ 5.0325e-01],
         [-1.7855e-01],
         [-8.7740e-02],
         [ 5.9960e-01],
         [-2.0503e-01],
         [-2.9960e-01],
         [ 8.7264e-02],
         [ 1.6665e-01],
         [ 3.8367

In [181]:
loss_history = []
def optimize_model():
    global loss_history
    if len(memory) < BATCH_SIZE:
        return
    
    transitions = memory.sample(BATCH_SIZE)
    # Transpose the batch (see https://stackoverflow.com/a/19343/3343043 for
    # detailed explanation). This converts batch-array of Transitions
    # to Transition of batch-arrays.
    batch = Transition(*zip(*transitions))
    # Compute a mask of non-final states and concatenate the batch elements
    # (a final state would've been the one after which simulation ended)
    # THIS DOES NOT MATTER NOW BUT SHOULD EVENTUALLY EDIT THIS
    non_final_mask = torch.tensor(tuple(map(lambda s: s is not None,
                                          batch.next_state)), device=device, dtype=torch.bool)
    non_final_next_states = torch.cat([s for s in batch.next_state
                                                if s is not None])
    non_final_next_states = non_final_next_states.unsqueeze(1)
    state_batch = torch.cat(batch.state)
    state_batch = state_batch.unsqueeze(1)
    action_batch = torch.cat(batch.action)
    reward_batch = torch.cat(batch.reward)

    # Compute Q(s_t, a) - the model computes Q(s_t), then we select the
    # columns of actions taken. These are the actions which would've been taken
    # for each batch state according to policy_net
    state_action_values = policy_net(state_batch).gather(1, ((N_ACTIONS-1)*action_batch).type(torch.long))
    next_state_values = torch.zeros(BATCH_SIZE, device=device)
    # Double Q implementation
    _, max_indices = policy_net(non_final_next_states).max(1, keepdim=True)
    next_state_values[non_final_mask] = target_net(non_final_next_states).gather(1, max_indices).squeeze(1)
    
    ## Compute the expected Q values
    #import pdb; pdb.set_trace()
    expected_state_action_values = (next_state_values * GAMMA) + reward_batch
    # Normalizing Q values
    max_Q_prime = torch.max(expected_state_action_values) 
    expected_state_action_values = 2 * expected_state_action_values / max_Q_prime - 1
    loss = F.mse_loss(state_action_values, expected_state_action_values.unsqueeze(1))
    loss_history.append(loss)
    optimizer.zero_grad()
    loss.backward()
    clip_grad_norm_(policy_net.parameters(), 1)
    optimizer.step()

In [182]:
num_episodes = int(1e4)
steps_done = 0
episode_durations = []
loss_history = []
traj_history = []
for i_episode in range(num_episodes):
    if i_episode % TARGET_UPDATE == 0: print(str(i_episode) + " ", end='')
    # Initialize the environment and state
    env.reset()
    state = torch.tensor([env.fish_population], device=device, dtype=torch.float)
    traj_history.append(state)
    for t in count():
        # Select and perform an action
        action = select_action(state)
        fish_population, reward, done, _ = env.step(action)
        reward = torch.Tensor([reward], device=device)

        # Observe new state
        if not done:
            next_state = torch.tensor([fish_population], \
                                      device=device, dtype=torch.float)
        else:
            next_state = None

        # Store the transition in memory
        memory.push(state, action, next_state, reward)

        # Move to the next state
        state = next_state
        traj_history.append(state)

        # Perform one step of the optimization (on the target network)
        optimize_model()
        if done:
            episode_durations.append(t + 1)
            break
    # Update the target network, copying all weights and biases in DQN
    if i_episode % TARGET_UPDATE == 0:
        target_net.load_state_dict(policy_net.state_dict())

print('Complete')

0 100 200 300 400 500 600 700 800 900 1000 1100 1200 1300 1400 1500 1600 1700 1800 1900 2000 2100 2200 2300 2400 2500 2600 2700 2800 2900 3000 3100 3200 3300 3400 3500 3600 3700 3800 3900 4000 4100 4200 4300 4400 4500 4600 4700 4800 4900 5000 5100 5200 5300 5400 5500 5600 5700 5800 5900 6000 6100 6200 6300 6400 6500 6600 6700 6800 6900 7000 7100 7200 7300 7400 7500 7600 7700 7800 7900 8000 8100 8200 8300 8400 8500 8600 8700 8800 8900 9000 9100 9200 9300 9400 9500 9600 9700 9800 9900 Complete


In [169]:
steps_done

995227

In [183]:
index, counts = np.unique([int(x[0]) for x in traj_history if x is not None], return_counts=True)
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='population',
                               y_axis_label='count')
plot.circle(index[:], counts[:], line_width=0.5, alpha=1)

bokeh.io.show(plot)

In [171]:
for param in policy_net.parameters():
    print(param.grad)

tensor([[-5.5179e-03],
        [-3.3793e-03],
        [-3.4496e-03],
        [ 1.9463e-04],
        [-1.1971e-04],
        [-1.0465e-02],
        [-1.0344e-04],
        [-1.4691e-02],
        [ 1.6524e-04],
        [ 1.8735e-02],
        [ 1.3202e-02],
        [ 9.3680e-03],
        [-2.1381e-04],
        [-9.3227e-05],
        [-1.5393e-04],
        [ 1.3782e-03],
        [-5.6114e-03],
        [-8.1577e-05],
        [ 2.9743e-03],
        [ 7.3292e-05],
        [ 1.4213e-02],
        [ 1.0847e-02],
        [-3.1046e-06],
        [ 1.6995e-04],
        [-1.7133e-04],
        [-1.0127e-02],
        [-1.6708e-02],
        [-1.7199e-03],
        [ 2.8493e-03],
        [-2.0939e-04],
        [ 2.8348e-06],
        [ 5.8828e-05],
        [-1.0179e-04],
        [-5.3660e-05],
        [-2.9666e-05],
        [-2.8775e-05],
        [-1.3107e-04],
        [-1.1816e-04],
        [ 1.3506e-04],
        [-1.6641e-04],
        [-2.9344e-05],
        [ 9.8499e-03],
        [-5.3659e-03],
        [ 2

In [531]:
torch.save(model.state_dict(), './_.pth')

In [68]:
model = DQN(1, 1000, N_ACTIONS).to(device)
model.load_state_dict(torch.load("best_performing_model_2.pth"))
model.eval()

DQN(
  (fc1): Linear(in_features=1, out_features=1000, bias=True)
  (fc2): Linear(in_features=1000, out_features=11, bias=True)
)

In [69]:
def take_Q_step(initial_state):
    max_index = model(torch.tensor([initial_state]).type(torch.float)).max(0)[1]
    return env.action_space[max_index]

In [70]:
n_samples = 100
# Set up plots
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='time',
                               y_axis_label='N')


env = gym.make('fishing-v0')
collapse_points = []
harvests = []
# 
for sample in range(n_samples):
    env.reset()
    sample_traj = [env.fish_population]
    for season in range(100):
        env.step(take_Q_step(env.fish_population))
        sample_traj.append(env.fish_population)
    harvests.append(env.reward)
    all(isinstance(x, int) for x in sample_traj)
    sample_traj = np.array(sample_traj)
    plot.line(range(len(sample_traj)), sample_traj, line_width=0.5, alpha=0.5)


bokeh.io.show(plot)
env.close()

In [828]:
np.mean(harvests)

1.0000000000000004

In [829]:
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='population',
                               y_axis_label='harvest selection')

v_take_Q_step = np.vectorize(take_Q_step)
x = np.linspace(0, 1e5, 10**5 + 1)
plot.line(x, 1e4 * v_take_Q_step(x), line_width=0.5, alpha=1)

bokeh.io.show(plot)

In [164]:
plot = bokeh.plotting.figure(plot_width=600,
                               plot_height=400,
                               x_axis_label='step',
                               y_axis_label='loss')
np_loss_history = np.array(list(map(lambda x: x.detach().numpy(), loss_history)))
plot.line(range(len(np_loss_history[::100])), np_loss_history[::100], line_width=0.5, alpha=1)

bokeh.io.show(plot)